# Интегрирование, квадратурныe формулы

v.02, mms, 29.11.2022/8.10.2024 

In [ ]:
# Вспоминаем.
# numpy.poly1d
# https://numpy.org/doc/stable/reference/routines.polynomials.poly1d.html
# Создание объекта-полинома из коэфициентов poly1d(c_or_r[, r, variable]):
#    p = np.poly1d([1, 2, 3]) 
# Фитирование данных (построение интерп.полинома степени deg)
#    np.polyfit(x, y, deg)
# polyval(p, x)  значение полинома p в точке x  <=> p(x)
# polyint(p[, m, k])  неопределенны интеграл, m-порядок интегрирования, k-константы
# polyder(p[, m])  возвращает производную указанного порядка m
# polymul(a1, a2)  произведение двух многочленов

# numpy.polynomial:
# https://numpy.org/doc/stable/reference/routines.polynomials.html
# P=numpy.polynomial.Polynomial(p)
#                   .fit
#                   .integ
#                   .polynomial.polyval(x, P) 
#                   .polynomial.polyint(P)

 ## Формулы Ньтона-Котеса

In [ ]:
# Для вычисления определенного интеграла можно 
# 1) задать на интервале интегрирования узлы и выполнить по ним 
#    интерполяцию подинтегральной функции полиномом (np.polyfit(x, y, deg))
# 2) произвести аналитическое интегрирование полинома (P=np.polyint(p))
# 3) вычислить разность значений первообразного полинома в пределах интегрирования 
#   ( np.polyval(P,b) - np.polyval(P,a))

In [7]:
# Пример. Интеграл sin(x) на [0,pi]  
import numpy as np

X=np.linspace(0,np.pi,6)
p=np.polyfit(X,np.sin(X),5)
P=np.polyint(p)
I=np.polyval(P,np.pi) - np.polyval(P,0)
print(f'I={I},  err={abs(I-2.0)}')

I=1.999203093915708,  err=0.0007969060842920594


In [ ]:
# Задание_1. Постройте график абсолютной величины погрешности от числа узлов N=2,...30
# в полулогарифмическом масштабе(plt.semilogy). 

In [ ]:
# Задание_2*. Повторить с интегралом 2xcos(x^2) на [0,5].
# Попробуйте объяснить, с чем связана такая большая погрешность.) 
# Подсказка(и мораль) - сначала на функцию посмотрите..

## Квадратурные формулы

In [ ]:
# cм. Integrals-doc.pdf п.1
# Вместо того, чтобы каждый раз для интегрируемой функции строить интерполяционный полином, удобнее 
# получить квадратурную формулу в виде суммы значений функции на некотором наборе точек интервала, 
# умноженной на весовые коэффициенты. Эти веса можно вычислять заранее по полиномам 
# Лагранжа (см. лекции Буслова). Ниже два варианта функции расчета весов. 

In [ ]:
import numpy as np

def lah1(a,b,N):
# Вычисление весовых коэф. в квадратур. формуле на основе numpy.poly1d
    X=np.linspace(a,b,N)
    F=np.eye(N)             # единичная матрица
    lambd=np.zeros(N)
    for k in range(0,N):
        p=np.polyfit(X,F[k,:],N-1)
        P=np.polyint(p)
        lambd[k]=np.polyval(P,b) - np.polyval(P,a)
    return lambd


In [ ]:
from numpy.polynomial import Polynomial as P

def lah2(a,b,N):
# Вычисление весовых коэф. в квадратур. формуле на основе numpy.polynomial.Polynomial
    X=np.linspace(a,b,N)
    F=np.eye(N)             # единичная матрица
    lambd=np.zeros(N)
    for k in range(0,N):
        c=P.fit(X,F[k,:],N-1)
        C=P.integ(c)
        lambd[k]=C(b)-C(a)
    return lambd

In [ ]:
# Посчитаем наш integral(sin(x)) [0,pi]  
X=np.linspace(0,np.pi,6)        # задаем равномерный набор из 6 точек
lahh1=lah1(0,np.pi,6)           # считаем коэффициенты
I=np.dot(np.sin(X),lahh1)       # считаем интеграл                
print("poly1d:    ", I, abs(I-2.0), lahh1)    # печатаем знaчение интеграла, погрешность и коэффициенты

#lahh2=lah2(0,np.pi,6)
#print("Polynomial:", np.dot(np.sin(X),lahh2), lahh2)      

In [ ]:
# Задание_3. Проверить, что np.sum(lambd) = b-a
sum(lahh1)     # =pi

## Ортогональные полиномы

In [ ]:
# Формулы наивысшей алгбраической степени точности строятся при помощи ортогональных полиномов.
# В качестве узлов квадратурной формулы выбираются нули ортогонального полинома, а коэф-ты  
# можно получить аналогично lah1, cм.выше.
# Возьмем ортогональные полиномы Лежандра из библиотеки scipy.special, 
# scipy.special.legendre(n), где n-cтепень многочлена

In [ ]:
# Пример: сгенерируем полином Лежандра 3-степени ( 1/2*(5x^3 + 0x^2 - 3x + 0)):

from scipy.special import legendre
p=legendre(3)     # -> poly1d([ 2.5,  0. , -1.5,  0. ])
print(p)
print(type(p))

print(p.coef)     # коэфициенты
print(p.roots)    # корни 

In [ ]:
# Посмотрим на графики полиномов Лежандра степени 1-5. 
# Все их корни лежат в [-1,1]

import matplotlib.pyplot as plt 

x = np.linspace(-1, 1, 100)
for k in range(1,6):
    p=legendre(k)
    plt.plot(x, p(x), label='n='+str(k))
plt.legend()
plt.grid()
plt.show()

In [ ]:
# Проверьте ортогональность. Для этого можно взять любой полином степени < N и 
# скалярно перемножить с ортогональным полиномом.
N=6
p=legendre(6)
P1=np.poly1d([1,2,3,4,5])
print(p)
print(P1)
print(np.polymul(p,P1))
GP=np.polyint(np.polymul(p,P1))
np.polyval(GP, -1) - np.polyval(GP, 1)     # интегрируем на интервале [-1,1] -> результат порядка 1e-16

In [ ]:
# П.Лежандра на [-1,1], поэтому для реальных задач нужно отображение [-1,1]->[a,b]  g=[(b-a)x+a+b]/2 
# т.е. найдем нужное число N корней на [-1,1] и отобразим в [a,b]. 

def lahort(a,b,N):
# Вычисление весовых коэф. в квадратур. формуле наивысшей алгбраической степени точности.
    r=legendre(N,monic=True).r         # корни полинома Лежандра на [-1,1]
    r.sort()
#    print("r.sort:",r)
    X=((b-a)*r+a+b)/2.0                # корни на [a,b]
    F=np.eye(N)                        # единичная матрица
    lambd=np.zeros(N)
    for k in range(0,N):
        p=np.polyfit(X,F[k,:],N-1)
        P=np.polyint(p)
        lambd[k]=np.polyval(P,b) - np.polyval(P,a) 
    return lambd, r, X

In [ ]:
[l_ort,r,R]=lahort(0,np.pi,5)
print(l_ort)         # весовыe коэф-ты lambd
print(r)             # корни на на [-1,1]
print(R)             # корни на [a,b]   
sum("Сумма lambd:", sum(l_ort))  # проверка: д.б. = длине интервала, т.е. pi

In [ ]:
# Cравним точность на одном том же числе узлов для интеграла sin(x) на [0,pi],
# + напечатаем веса и узлы.
X=np.linspace(0,np.pi,5)
lahh1=lah1(0,np.pi,5)
print("lah1:  ", np.dot(np.sin(X),lahh1),'\n', lahh1,'\n', X, '\n')          
print("lahort:", np.dot(np.sin(R),l_ort),'\n', l_ort, '\n', R) 

In [ ]:
# Задание_3. Вычислите интеграл log(x)/x на [0.5, 1.5] c точностью  10e-8

In [ ]:
# Задание_4. Для интеграла из Задания_3 сравните погрешность по квадратурной формуле с 
# равномерным распределением корней на интервале и при использовании корней ортогонального полинома. 


### Задание_5
Вычислите интеграл  $\int\limits_1^{1.6} \frac{2x}{x^2-4}\,dx,$  используя квадратурную формулу.  Сравните погрешности для разных  $N$ (от 4 до 10),  получаемые при использовании равноотстоящих узлов и узлов в корнях ортогональных полиномов. (Предварительно найдите точное значение интеграла самостоятельно любым способом).

## Замечание о символьных вычислениях(sympy) или как аналитически вычислить интеграл

In [ ]:
# Символические вычисления бывают полезны)

from sympy import *
from IPython.display import display
init_printing()

w=Symbol('w')
display(integrate(log(w)/w,w))            # log(x^2)/2
a4=integrate(log(w)/w,(w,0.5,1.5))
print(a4)                                 # -0.158025530012518

## Примеры квадратурных формул. Cоставные формулы. Задание_6(!)

In [ ]:
# См. Integrals-doc.pdf п.3  и лекции Буслова п.4.4

# Задание_6. Реализуйте все составные формулы из Integrals-doc.pdf п.3.
# Найдите число узлов N и шаг h, при котором точность вычисления интеграла из Задяния_5 
# станет 1e-5 по всем реализованным составным формулам. 
# Выведите результаты для каждого метода в виде: Метод  N   h   I   Err.